In [31]:
import pandas as pd
import seaborn as sns
import numpy as np

from shapely.geometry import Point
import geopandas as gpd

import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

from src.config import DADOS_LIMPOS, DADOS_GEO_ORIGINAIS, DADOS_GEO_MEDIAN

In [2]:
df = pd.read_parquet(DADOS_LIMPOS)

df.head()

longitude   latitude  housing_median_age  total_rooms  total_bedrooms  \
0 -122.230003  37.880001                  41          880             129   
1 -122.220001  37.860001                  21         7099            1106   
2 -122.260002  37.840000                  42         2555             665   
3 -122.260002  37.849998                  50         1120             283   
4 -122.260002  37.840000                  50         2239             455   

   population  households  median_income  median_house_value ocean_proximity  \
0         322         126         8.3252              452600        NEAR BAY   
1        2401        1138         8.3014              358500        NEAR BAY   
2        1206         595         2.0804              226700        NEAR BAY   
3         697         264         2.1250              140000        NEAR BAY   
4         990         419         1.9911              158700        NEAR BAY   

   median_income_cat  rooms_per_household  population_per_household  \
0                  5             6.984127                  2.555556   
1                  5             6.238137                  2.109842   
2                  2             4.294117                  2.026891   
3                  2             4.242424                  2.640152   
4                  2             5.343676                  2.362768   

   bedroomns_per_room  
0            0.146591  
1            0.155797  
2            0.260274  
3            0.252679  
4            0.203216

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17564 entries, 0 to 17563
Data columns (total 14 columns):
 #   Column                    Non-Null Count  Dtype   
---  ------                    --------------  -----   
 0   longitude                 17564 non-null  float32 
 1   latitude                  17564 non-null  float32 
 2   housing_median_age        17564 non-null  int8    
 3   total_rooms               17564 non-null  int16   
 4   total_bedrooms            17564 non-null  int16   
 5   population                17564 non-null  int16   
 6   households                17564 non-null  int16   
 7   median_income             17564 non-null  float32 
 8   median_house_value        17564 non-null  int32   
 9   ocean_proximity           17564 non-null  category
 10  median_income_cat         17564 non-null  int64   
 11  rooms_per_household       17564 non-null  float32 
 12  population_per_household  17564 non-null  float32 
 13  bedroomns_per_room        17564 non-null  floa

In [4]:
fig = px.scatter_map(df, lat='latitude', lon="longitude",
                        color_discrete_sequence=["fuchsia"], zoom=3, height=500, width=800, template='plotly_dark')
fig.update_layout(map_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [5]:
fig = px.scatter_map(df, lat='latitude', lon='longitude', color='median_income_cat', zoom=3, height=500, width=800, template='plotly_dark')
fig.update_layout(map_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [6]:
fig = px.scatter_map(df, lat='latitude', lon='longitude', color='median_house_value', zoom=3, height=500, width=800, template='plotly_dark')
fig.update_layout(map_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [7]:
cities = gpd.read_file(DADOS_GEO_ORIGINAIS)

In [8]:
cities = cities.to_crs(epsg=32610)
cities["centroid"] = cities.centroid
cities["centroid"] = cities["centroid"].to_crs(cities.crs)

In [9]:
geometry = df.apply(lambda row: Point(row['longitude'], row['latitude']), axis=1)

gdf_points = gpd.GeoDataFrame(df, geometry=geometry, crs="EPSG:4326")

gdf_points = gdf_points.to_crs(epsg=32610)

gdf_joined = gpd.sjoin(gdf_points, cities, how="left", predicate="within")

gdf_joined = gdf_joined.to_crs(epsg=32610)

In [10]:
gdf_joined.isnull().any(axis=1).sum()

186

In [11]:
linhas_faltantes = gdf_joined[gdf_joined.isnull().any(axis=1)].index
linhas_faltantes

Index([   45,   265,   266,   308,   312,   313,   317,   318,   320,   412,
       ...
       15752, 15755, 15756, 15942, 15970, 17198, 17199, 17201, 17232, 17258],
      dtype='int64', length=186)

In [12]:
def condado_mais_proximo(linha):
    ponto = linha['geometry']
    distancias = cities['centroid'].distance(ponto)
    idx_condado_proximo = distancias.idxmin()
    condado_proximo = cities.loc[idx_condado_proximo]
    return condado_proximo["name"]

In [13]:
condado_mais_proximo(gdf_joined.loc[308])

'San Francisco'

In [14]:
gdf_joined.loc[linhas_faltantes, ["name"]] = gdf_joined.loc[linhas_faltantes].apply(condado_mais_proximo, axis=1)

In [15]:
gdf_joined.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 17564 entries, 0 to 17563
Data columns (total 21 columns):
 #   Column                    Non-Null Count  Dtype              
---  ------                    --------------  -----              
 0   longitude                 17564 non-null  float32            
 1   latitude                  17564 non-null  float32            
 2   housing_median_age        17564 non-null  int8               
 3   total_rooms               17564 non-null  int16              
 4   total_bedrooms            17564 non-null  int16              
 5   population                17564 non-null  int16              
 6   households                17564 non-null  int16              
 7   median_income             17564 non-null  float32            
 8   median_house_value        17564 non-null  int32              
 9   ocean_proximity           17564 non-null  category           
 10  median_income_cat         17564 non-null  int64              
 11  rooms_per_ho

In [16]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17564 entries, 0 to 17563
Data columns (total 14 columns):
 #   Column                    Non-Null Count  Dtype   
---  ------                    --------------  -----   
 0   longitude                 17564 non-null  float32 
 1   latitude                  17564 non-null  float32 
 2   housing_median_age        17564 non-null  int8    
 3   total_rooms               17564 non-null  int16   
 4   total_bedrooms            17564 non-null  int16   
 5   population                17564 non-null  int16   
 6   households                17564 non-null  int16   
 7   median_income             17564 non-null  float32 
 8   median_house_value        17564 non-null  int32   
 9   ocean_proximity           17564 non-null  category
 10  median_income_cat         17564 non-null  int64   
 11  rooms_per_household       17564 non-null  float32 
 12  population_per_household  17564 non-null  float32 
 13  bedroomns_per_room        17564 non-null  floa

In [17]:
df['city'] = gdf_joined['name']


df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17564 entries, 0 to 17563
Data columns (total 15 columns):
 #   Column                    Non-Null Count  Dtype   
---  ------                    --------------  -----   
 0   longitude                 17564 non-null  float32 
 1   latitude                  17564 non-null  float32 
 2   housing_median_age        17564 non-null  int8    
 3   total_rooms               17564 non-null  int16   
 4   total_bedrooms            17564 non-null  int16   
 5   population                17564 non-null  int16   
 6   households                17564 non-null  int16   
 7   median_income             17564 non-null  float32 
 8   median_house_value        17564 non-null  int32   
 9   ocean_proximity           17564 non-null  category
 10  median_income_cat         17564 non-null  int64   
 11  rooms_per_household       17564 non-null  float32 
 12  population_per_household  17564 non-null  float32 
 13  bedroomns_per_room        17564 non-null  floa

In [18]:
df.head()

longitude   latitude  housing_median_age  total_rooms  total_bedrooms  \
0 -122.230003  37.880001                  41          880             129   
1 -122.220001  37.860001                  21         7099            1106   
2 -122.260002  37.840000                  42         2555             665   
3 -122.260002  37.849998                  50         1120             283   
4 -122.260002  37.840000                  50         2239             455   

   population  households  median_income  median_house_value ocean_proximity  \
0         322         126         8.3252              452600        NEAR BAY   
1        2401        1138         8.3014              358500        NEAR BAY   
2        1206         595         2.0804              226700        NEAR BAY   
3         697         264         2.1250              140000        NEAR BAY   
4         990         419         1.9911              158700        NEAR BAY   

   median_income_cat  rooms_per_household  population_per_household  \
0                  5             6.984127                  2.555556   
1                  5             6.238137                  2.109842   
2                  2             4.294117                  2.026891   
3                  2             4.242424                  2.640152   
4                  2             5.343676                  2.362768   

   bedroomns_per_room     city  
0            0.146591  Alameda  
1            0.155797  Alameda  
2            0.260274  Alameda  
3            0.252679  Alameda  
4            0.203216  Alameda

In [19]:
df['median_income_cat'].value_counts()

df['median_income_cat'] = df['median_income_cat'].astype("category")

In [20]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17564 entries, 0 to 17563
Data columns (total 15 columns):
 #   Column                    Non-Null Count  Dtype   
---  ------                    --------------  -----   
 0   longitude                 17564 non-null  float32 
 1   latitude                  17564 non-null  float32 
 2   housing_median_age        17564 non-null  int8    
 3   total_rooms               17564 non-null  int16   
 4   total_bedrooms            17564 non-null  int16   
 5   population                17564 non-null  int16   
 6   households                17564 non-null  int16   
 7   median_income             17564 non-null  float32 
 8   median_house_value        17564 non-null  int32   
 9   ocean_proximity           17564 non-null  category
 10  median_income_cat         17564 non-null  category
 11  rooms_per_household       17564 non-null  float32 
 12  population_per_household  17564 non-null  float32 
 13  bedroomns_per_room        17564 non-null  floa

In [21]:
df['city'].value_counts()

city
Los Angeles        4831
San Diego          1466
Orange             1435
Santa Clara         824
Alameda             730
San Bernardino      729
Sacramento          622
Contra Costa        550
Riverside           504
Fresno              490
San Joaquin         387
Kern                353
Ventura             342
San Mateo           335
Sonoma              294
Stanislaus          282
Santa Barbara       262
Tulare              246
San Francisco       233
Santa Cruz          186
Solano              176
Monterey            167
Butte               144
San Luis Obispo     131
Merced              123
Marin               121
Shasta              119
Imperial            115
Humboldt            109
Placer              102
El Dorado           100
Napa                 94
Kings                86
Lake                 81
Nevada               80
Mendocino            76
Madera               75
Yolo                 74
Sutter               56
Yuba                 51
Tehama               47
Tuolumne   

In [22]:
fig = px.scatter_map(df, lat='latitude', lon='longitude', color='city', zoom=3, height=500, width=800, template='plotly_dark')
fig.update_layout(map_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [23]:
df_per_city = df.groupby("city").median(numeric_only=True).reset_index()

df_per_city

city   longitude   latitude  housing_median_age  total_rooms  \
0           Alameda -122.129997  37.709999                35.0       1938.0   
1            Alpine -119.860001  38.824997                18.5       1407.5   
2            Amador -120.720001  38.430000                17.0       1787.0   
3             Butte -121.599998  39.709999                22.0       1875.0   
4         Calaveras -120.559998  38.200001                17.0       2745.0   
5            Colusa -122.044998  39.180000                34.0       1497.0   
6      Contra Costa -122.059998  37.950001                27.0       2399.5   
7         Del Norte -124.169998  41.764999                19.0       2705.5   
8         El Dorado -120.709999  38.759998                17.0       2244.0   
9            Fresno -119.769997  36.759998                24.0       1923.5   
10            Glenn -122.190002  39.665001                23.0       1564.5   
11         Humboldt -124.110001  40.779999                30.0       1927.0   
12         Imperial -115.559998  32.810001                21.0       1311.0   
13             Inyo -118.349998  37.299999                21.5       2385.5   
14             Kern -119.000000  35.369999                28.0       2185.0   
15            Kings -119.660004  36.310001                25.0       1548.5   
16             Lake -122.730003  38.980000                18.0       1410.0   
17           Lassen -120.580002  40.410000                19.0       1707.0   
18      Los Angeles -118.239998  34.029999                35.0       1909.0   
19           Madera -120.059998  36.980000                18.0       1995.0   
20            Marin -122.540001  37.980000                32.0       2846.0   
21         Mariposa -119.949997  37.509998                15.0       2116.0   
22        Mendocino -123.330002  39.294998                23.0       1733.0   
23           Merced -120.610001  37.320000                21.0       2003.0   
24            Modoc -120.529999  41.575001                22.0       2472.0   
25             Mono -118.980003  37.675003                16.0       1935.0   
26         Monterey -121.709999  36.610001                27.0       2392.0   
27             Napa -122.305000  38.320000                25.0       2020.5   
28           Nevada -121.055000  39.215000                14.0       1876.5   
29           Orange -117.910004  33.759998                23.0       2421.0   
30           Placer -121.180000  38.869999                17.0       2720.5   
31           Plumas -120.910004  39.930000                21.0       1511.0   
32        Riverside -117.230003  33.875000                19.0       2696.0   
33       Sacramento -121.379997  38.599998                25.0       2436.5   
34       San Benito -121.400002  36.845001                18.5       2200.5   
35   San Bernardino -117.320000  34.110001                21.0       2512.0   
36        San Diego -117.110001  32.799999                21.0       2362.0   
37    San Francisco -122.449997  37.740002                43.0       2082.0   
38      San Joaquin -121.279999  37.970001                27.0       1853.0   
39  San Luis Obispo -120.660004  35.290001                17.0       2949.0   
40        San Mateo -122.320000  37.560001                35.0       2367.0   
41    Santa Barbara -120.115005  34.614998                25.0       1994.5   
42      Santa Clara -121.919998  37.330002                25.0       2466.5   
43       Santa Cruz -121.989998  36.980000                26.5       2104.5   
44           Shasta -122.349998  40.570000                19.0       2251.0   
45           Sierra -120.239998  39.610001                32.0       1404.0   
46         Siskiyou -122.544998  41.614998                23.0       2372.0   
47           Solano -122.029999  38.259998                21.0       2502.0   
48           Sonoma -122.709999  38.419998                23.0       2393.0   
49       Stanislaus -120.970001  37.639999                26.0   

In [24]:
df_per_city.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 58 entries, 0 to 57
Data columns (total 13 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   city                      58 non-null     object 
 1   longitude                 58 non-null     float32
 2   latitude                  58 non-null     float32
 3   housing_median_age        58 non-null     float64
 4   total_rooms               58 non-null     float64
 5   total_bedrooms            58 non-null     float64
 6   population                58 non-null     float64
 7   households                58 non-null     float64
 8   median_income             58 non-null     float32
 9   median_house_value        58 non-null     float64
 10  rooms_per_household       58 non-null     float32
 11  population_per_household  58 non-null     float32
 12  bedroomns_per_room        58 non-null     float32
dtypes: float32(6), float64(6), object(1)
memory usage: 4.7+ KB


In [25]:
couty_ocean_prox = df[['city', "ocean_proximity"]].groupby('city').agg(pd.Series.mode)

In [26]:
df_per_city = df_per_city.merge(couty_ocean_prox, left_on='city', right_index=True)


df_per_city.head()

city   longitude   latitude  housing_median_age  total_rooms  \
0    Alameda -122.129997  37.709999                35.0       1938.0   
1     Alpine -119.860001  38.824997                18.5       1407.5   
2     Amador -120.720001  38.430000                17.0       1787.0   
3      Butte -121.599998  39.709999                22.0       1875.0   
4  Calaveras -120.559998  38.200001                17.0       2745.0   

   total_bedrooms  population  households  median_income  median_house_value  \
0           399.0      1038.5       380.5        3.57265            188500.0   
1           334.0       402.5       203.5        2.00180            165050.0   
2           357.0       767.0       305.0        3.04650            116700.0   
3           372.5       936.5       356.5        2.31895             86450.0   
4           559.0      1061.0       459.0        2.56670            101600.0   

   rooms_per_household  population_per_household  bedroomns_per_room  \
0             5.091506                  2.724138            0.206806   
1             7.331940                  2.027528            0.236384   
2             6.058824                  2.435115            0.191900   
3             5.308164                  2.514830            0.199470   
4             5.994983                  2.488000            0.204878   

  ocean_proximity  
0        NEAR BAY  
1          INLAND  
2          INLAND  
3          INLAND  
4          INLAND

Para trabalhar com mapas de divisão de cidades o plotly já tem o mapa choropleth que é muito bom é totalmente personalizado assim como todos os mapas do plotly
Para ele funcionar diferente das bibliotecas acima precisamos carregar o geojson em uma variavel

In [27]:
import json
from pathlib import Path

path_geo = Path(DADOS_GEO_ORIGINAIS)

with open(path_geo, "r", encoding="utf-8") as f:
    geojson_data = json.load(f)

In [28]:
fig = px.choropleth(df_per_city, geojson=geojson_data, locations='city', color='median_house_value', featureidkey="properties.name",
                           scope="usa")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [29]:
fig = px.choropleth(df_per_city, geojson=geojson_data, locations="city", featureidkey="properties.name", color="median_house_value", projection="mercator")
fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [30]:
fig = px.scatter_map(df, lat="latitude", lon="longitude", color="median_house_value", hover_name="city", zoom=6, height=500, width=800, template="plotly_dark")
fig.update_layout(map_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()


In [32]:
df_per_city.to_parquet(DADOS_GEO_MEDIAN, index=False)